In [59]:
import pandas as pd
from pandas import DataFrame
from scipy.stats import zscore
import numpy as np
from numpy import mean
from numpy import std
from sklearn.model_selection import cross_val_score
from sklearn.model_selection import RepeatedStratifiedKFold
from sklearn.preprocessing import LabelEncoder
from sklearn.preprocessing import StandardScaler
from sklearn.pipeline import Pipeline
from sklearn.model_selection import KFold
from matplotlib import pyplot
from itertools import combinations
from pandas import DataFrame
from sklearn.preprocessing import PolynomialFeatures
from sklearn.ensemble import GradientBoostingRegressor
import lightgbm as xgb
from lightgbm import LGBMRegressor
from sklearn.datasets import load_boston
from sklearn.model_selection import train_test_split
from sklearn.model_selection import cross_val_score, KFold
from sklearn.metrics import mean_squared_error
import matplotlib.pyplot as plt
from sklearn.model_selection import RepeatedKFold
from numpy import absolute

In [60]:
#Removing empty columns and splitting X and Y from the rest of the dataset
df = pd.read_excel('new_df_66.xlsx', engine='openpyxl')

In [61]:
new_df_1 = df.drop(['ile', 'ile_st', 'trp', 'trp_st', 'h_pi', 'X.w', 'MSWHIM3.1','DELTA30', 'PP2.1'], axis=1)
Y = df['DELTA30']

In [62]:
#% removing correlated features
correlated_features= set()
correlation_matrix = new_df_1.corr()
for i in range(len(correlation_matrix.columns)):
    for j in range(i):
        if abs(correlation_matrix.iloc[i, j]) > 0.90:
            colname = correlation_matrix.columns[i]
            correlated_features.add(colname)

In [63]:
correlated_features

{'BLOSUM1.1',
 'F2.1',
 'KF2.1',
 'KF4.1',
 'MSWHIM1.1',
 'ProtFP1.1',
 'ProtFP2.1',
 'ST1.1',
 'T1.1',
 'VHSE1.1',
 'VHSE3.1',
 'VHSE5.1',
 'convex_hull_volume',
 'glu_st',
 'leu_st',
 'mean_as_solv_acc_st',
 'met_st',
 'phe_st',
 'pock_asa',
 'pock_asa22',
 'pock_asa_st',
 'pock_pol_asa',
 'prop_polar_atm_st',
 'rmsd_bs_ca',
 'rmsd_bs_ca_sd',
 'rmsd_pro_bb',
 'rmsd_pro_bb_st',
 'rmsd_pro_ca',
 'rmsd_pro_ca_sd',
 'rog_bs_bb',
 'rog_bs_bb_sd',
 'rog_bs_ca',
 'rog_bs_ca_sd',
 'rog_bs_noh',
 'rog_bs_noh_sd',
 'rog_pro_bb',
 'rog_pro_bb_sd',
 'rog_pro_ca',
 'rog_pro_ca_sd',
 'rog_pro_noh_sd',
 'volume_score_st'}

In [64]:
# new_df_1.drop(correlated_features, axis=1, inplace=True)
# new_df_1

In [65]:
new_df_1.describe()


pock_volume  pock_volume_st  pock_asa  pock_asa_st  pock_pol_asa  \
count       312.00          312.00    312.00       312.00        312.00   
mean        429.39          138.22    271.71        81.54        154.26   
std          61.38           15.60     39.51         9.77         24.92   
min         254.25           91.69    155.09        53.44         87.17   
25%         391.98          127.41    247.38        75.35        139.29   
50%         437.45          137.36    274.20        80.83        155.02   
75%         468.57          148.30    294.71        86.87        170.11   
max         597.88          179.46    394.39       112.65        230.70   

       pock_pol_asa_st  pock_apol_asa  pock_apol_asa_st  pock_asa22  \
count           312.00         312.00            312.00      312.00   
mean             50.04         117.45             41.32      145.67   
std               6.35          19.97              5.18       20.70   
min              30.33          61.69             24.93       89.52   
25%              46.14         104.83             37.72      130.57   
50%              49.39         117.06             41.47      147.29   
75%              54.25         129.56             44.93      158.57   
max              71.48         180.84             57.72      204.40   

       pock_asa22_st  ...  BLOSUM3.1  BLOSUM4.1  BLOSUM5.1  BLOSUM6.1  \
count         312.00  ...     312.00     312.00     312.00     312.00   
mean           54.04  ...     -13.12      -1.51      -8.65      22.82   
std             5.47  ...       1.11       0.73       1.17       1.04   
min            38.21  ...     -15.80      -3.23     -12.43      19.78   
25%            50.64  ...     -13.76      -2.01      -9.29      22.23   
50%            53.72  ...     -13.43      -1.68      -8.50      22.58   
75%            57.46  ...     -12.51      -1.14      -7.82      23.20   
max            69.72  ...      -8.75       1.14      -5.80      26.48   

       BLOSUM7.1  BLOSUM8.1  BLOSUM9.1  BLOSUM10.1  MSWHIM1.1  MSWHIM2.1  
count     312.00     312.00     312.00      312.00     312.00     312.00  
mean       10.86      -3.11      18.96       16.64     -63.65      98.34  
std         1.12       1.56       0.95        1.11       1.09       0.99  
min         6.70     -10.51      16.37       13.12     -66.86      95.84  
25%        10.28      -3.88      18.35       15.92     -64.20      97.79  
50%        11.05      -2.95      18.85       16.80     -63.85      98.35  
75%        11.34      -2.09      19.62       17.40     -63.05      98.73  
max        14.48       0.13      21.81       19.01     -60.21     103.75  

[8 rows x 184 columns]

In [66]:
df.columns.get_loc("val_st")

79

In [67]:
# histograms of the variables
new_df_1.hist(figsize=(200,200))
pyplot.show()


In [68]:
from sklearn.preprocessing import PowerTransformer
pt = PowerTransformer(method='yeo-johnson')
data = pt.fit_transform(new_df_1)
data = DataFrame(data)
data.hist(figsize=(200,200))
pyplot.savefig('dataset_yeo-johnson.png')
pyplot.show()


In [69]:
data.describe()


0      1      2      3      4      5      6      7      8      9    \
count 312.00 312.00 312.00 312.00 312.00 312.00 312.00 312.00 312.00 312.00   
mean   -0.00   0.00   0.00   0.00   0.00   0.00   0.00  -0.00  -0.00   0.00   
std     1.00   1.00   1.00   1.00   1.00   1.00   1.00   1.00   1.00   1.00   
min    -2.53  -3.25  -2.71  -3.36  -2.64  -3.44  -2.78  -3.25  -2.64  -3.08   
25%    -0.65  -0.68  -0.64  -0.61  -0.61  -0.60  -0.63  -0.69  -0.74  -0.61   
50%     0.09  -0.03   0.03  -0.03   0.02  -0.07  -0.02   0.04   0.07  -0.04   
75%     0.62   0.66   0.57   0.58   0.63   0.68   0.61   0.70   0.62   0.64   
max     3.10   2.51   3.39   2.84   3.13   3.13   3.20   3.12   2.92   2.74   

       ...    174    175    176    177    178    179    180    181    182  \
count  ... 312.00 312.00 312.00 312.00 312.00 312.00 312.00 312.00 312.00   
mean   ...  -0.00  -0.00  -0.00  -0.00   0.00  -0.00  -0.00   0.00   0.00   
std    ...   1.00   1.00   1.00   1.00   1.00   1.00   1.00   1.00   1.00   
min    ...  -3.40  -3.21  -2.69  -4.43  -3.39  -3.33  -2.81  -2.40  -3.16   
25%    ...  -0.52  -0.69  -0.61  -0.52  -0.54  -0.61  -0.64  -0.74  -0.49   
50%    ...  -0.17  -0.13   0.05  -0.13   0.14  -0.03  -0.10   0.03  -0.16   
75%    ...   0.69   0.67   0.68   0.49   0.41   0.60   0.70   0.65   0.57   
max    ...   2.63   2.43   3.01   2.66   3.47   3.26   2.89   2.73   2.97   

         183  
count 312.00  
mean   -0.03  
std     1.00  
min    -2.86  
25%    -0.57  
50%     0.04  
75%     0.43  
max     4.66  

[8 rows x 184 columns]

In [70]:
cols = new_df_1.columns.tolist()
data.columns = cols
data.describe()

pock_volume  pock_volume_st  pock_asa  pock_asa_st  pock_pol_asa  \
count       312.00          312.00    312.00       312.00        312.00   
mean         -0.00            0.00      0.00         0.00          0.00   
std           1.00            1.00      1.00         1.00          1.00   
min          -2.53           -3.25     -2.71        -3.36         -2.64   
25%          -0.65           -0.68     -0.64        -0.61         -0.61   
50%           0.09           -0.03      0.03        -0.03          0.02   
75%           0.62            0.66      0.57         0.58          0.63   
max           3.10            2.51      3.39         2.84          3.13   

       pock_pol_asa_st  pock_apol_asa  pock_apol_asa_st  pock_asa22  \
count           312.00         312.00            312.00      312.00   
mean              0.00           0.00             -0.00       -0.00   
std               1.00           1.00              1.00        1.00   
min              -3.44          -2.78             -3.25       -2.64   
25%              -0.60          -0.63             -0.69       -0.74   
50%              -0.07          -0.02              0.04        0.07   
75%               0.68           0.61              0.70        0.62   
max               3.13           3.20              3.12        2.92   

       pock_asa22_st  ...  BLOSUM3.1  BLOSUM4.1  BLOSUM5.1  BLOSUM6.1  \
count         312.00  ...     312.00     312.00     312.00     312.00   
mean            0.00  ...      -0.00      -0.00      -0.00      -0.00   
std             1.00  ...       1.00       1.00       1.00       1.00   
min            -3.08  ...      -3.40      -3.21      -2.69      -4.43   
25%            -0.61  ...      -0.52      -0.69      -0.61      -0.52   
50%            -0.04  ...      -0.17      -0.13       0.05      -0.13   
75%             0.64  ...       0.69       0.67       0.68       0.49   
max             2.74  ...       2.63       2.43       3.01       2.66   

       BLOSUM7.1  BLOSUM8.1  BLOSUM9.1  BLOSUM10.1  MSWHIM1.1  MSWHIM2.1  
count     312.00     312.00     312.00      312.00     312.00     312.00  
mean        0.00      -0.00      -0.00        0.00       0.00      -0.03  
std         1.00       1.00       1.00        1.00       1.00       1.00  
min        -3.39      -3.33      -2.81       -2.40      -3.16      -2.86  
25%        -0.54      -0.61      -0.64       -0.74      -0.49      -0.57  
50%         0.14      -0.03      -0.10        0.03      -0.16       0.04  
75%         0.41       0.60       0.70        0.65       0.57       0.43  
max         3.47       3.26       2.89        2.73       2.97       4.66  

[8 rows x 184 columns]

In [71]:
model = xgb.(verbosity=0)
cv = RepeatedKFold(n_splits=10, n_repeats=3, random_state=101)
scores = cross_val_score(model, data, Y, scoring='neg_mean_absolute_error', cv=cv, n_jobs=1)
scores = absolute(scores)
print('Mean MAE: %.3f (%.3f)' % (scores.mean(), scores.std()))

SyntaxError: invalid syntax (<ipython-input-71-751ed6447b8b>, line 1)

In [ ]:
# # Polynomial combination of features
# poly = PolynomialFeatures(2)
# data = poly.fit_transform(data)
# dataset = DataFrame(data)
# num_instances = 3
# num_folds = 6
# seed = 4236
# scoring = "neg_mean_absolute_error"
# models = get_models()
# results, names = list(), list()
# for name, model in models.items():
#     scores = evaluate_model(model, data, Y)
#     results.append(scores)
#     names.append(name)
#     print('>%s %.3f (%.3f)' % (name, mean(scores), std(scores)))
#

In [ ]:
# pyplot.boxplot(results, labels=names, showmeans=True)
# pyplot.xlabel('Polynomial Degree')
# pyplot.ylabel('Negative Mean Absolute Error')
# pyplot.savefig("Box-poly.jpg")
# pyplot.show()
#

In [ ]:
# # define dataset
# X, y = get_dataset()
# # calculate change in number of features
# num_features = list()
# degress = [i for i in range(1, 4)]
# for d in degress:
# 	# create transform
# 	trans = PolynomialFeatures(degree=d)
# 	# fit and transform
# 	data = trans.fit_transform(X)
# 	# record number of features
# 	num_features.append(data.shape[1])
# 	# summarize
# 	print('Degree: %d, Features: %d' % (d, data.shape[1]))
# # plot degree vs number of features
#
#

In [ ]:
# z = [1, 2, 3]
# pyplot.plot(degress, num_features)
# pyplot.xlabel('Polynomial Degree')
# pyplot.ylabel('Number of Features')
# for i, txt in enumerate(num_features):
#     pyplot.annotate(txt, (z[i], num_features[i]), textcoords="offset pixels", # how to position the text
#                  xytext=(3,2), # distance from text to points (x,y)
#                  ha='center')
# pyplot.savefig("Number_Of_Features.jpg")
# pyplot.show()
#

In [ ]:
# new_df = add_interactions(X)
# scaler = StandardScaler()
# new_df_scaled = scaler.fit_transform(new_df)
# data = pd.DataFrame(new_df_scaled, columns=new_df.columns)
# data

In [ ]:
# data_1 = data.iloc[:, :30]
# data_2 = data.iloc[:, 30:60]
# data_3 = data.iloc[:, 60:90]
# data_4 = data.iloc[:, 90:120]
# data_5 = data.iloc[:, 120:]


In [ ]:
# data_1.to_csv("preprocessed_data_1.csv", header=True, index=False)
# data_2.to_csv("preprocessed_data_2.csv", header=True, index=False)
# data_3.to_csv("preprocessed_data_3.csv", header=True, index=False)
# data_4.to_csv("preprocessed_data_4.csv", header=True, index=False)
# data_5.to_csv("preprocessed_data_5.csv", header=True, index=False)
data.to_csv("prepocessed_data.csv", header=True, index=False)

In [ ]:
from lazypredict.Supervised import LazyRegressor
from sklearn.model_selection import train_test_split
#
X = data
Y


X_train, X_test, y_train, y_test = train_test_split(X, Y, test_size=.2, random_state=42)

In [ ]:
#fit all models
reg = LazyRegressor(predictions=True)
models, predictions = reg.fit(X_train, X_test, y_train, y_test)

In [ ]:
# models = pd.DataFrame(models)
#

In [ ]:
models

In [ ]:
data_preprocessed = pd.concat([X,Y], axis=1)
data_preprocessed.head()
data_preprocessed.to_csv("preprop_and_target.csv", header=True, index=False)

In [ ]:
seed = 7
test_size = 0.2

X_train, X_test, y_train, y_test = train_test_split(X, Y, test_size=0.2, random_state=seed)
model = xgb.LGBMRegressor(verbosity=0)
eval_set = [(X_train, y_train), (X_test, y_test)]
model.fit(X_train, y_train, eval_metric=["mae", "rmse"], eval_set=eval_set, verbose=True, early_stopping_rounds=10)
y_pred = model.predict(X_test)
predictions = [value for value in y_pred]
predictions
results = model.evals_result()
epoch = len(results['validation_0']['mae'])
x_axis = range(0, epoch)
# plot log loss
fig, ax = pyplot.subplots()
ax.plot(x_axis, results['validation_0']['mae'], label='Train')
ax.plot(x_axis, results['validation_1']['mae'], label='Test')
ax.legend()
pyplot.ylabel('Mean Absolute Error')
pyplot.title('XGBoost MAE')
pyplot.savefig('XGBoost_MAE_raw.png')
pyplot.show()
# plot classification error
fig, ax = pyplot.subplots()
ax.plot(x_axis, results['validation_0']['rmse'], label='Train')
ax.plot(x_axis, results['validation_1']['rmse'], label='Test')
ax.legend()
pyplot.ylabel('Root Mean Square Error')
pyplot.title('XGBoost RMSE')
pyplot.savefig('XGBoost_RMSE_raw.png')
pyplot.show()

In [ ]:
import xgboost as xgb
from sklearn.metrics import mean_absolute_error
from sklearn.metrics import r2_score
from sklearn.model_selection import RandomizedSearchCV
from sklearn.metrics import mean_absolute_error
from sklearn.metrics import fbeta_score, make_scorer


parameters = {'objective':['reg:squarederror'],
              'booster':['gbtree','gblinear'],
              'learning_rate': [0.001,0.004,0.008,0.01,0.02,0.03,0.04,0.05,0.06,0.07,
                                0.08,0.09,0.1,0.2,0.4,0.6,0.8,1],
              'max_depth': range(1,100,10),
              'min_child_weight': range(5,100,5),
              'colsample_bytree': [0.1,0.2,0.4,0.8,1],
              'n_estimators': range(10,1000,10),
              "reg_alpha"   : [0.1,0.2,0.4,0.6,0.8,1],
              "reg_lambda"  : range(1,10,1),
              "gamma"       : range(1,10,1)}

xgb_model = LGBMRegressor(random_state=7)

grid_obj_xgb = RandomizedSearchCV(xgb_model,parameters, cv=5,n_iter=15,scoring='neg_mean_absolute_error',verbose=5,n_jobs=12)
grid_obj_xgb.fit(X_train, y_train,verbose = 1)

y_pred_train = grid_obj_xgb.predict(X_train)
y_pred_test = grid_obj_xgb.predict(X_test)

err_xgb_train=mean_absolute_error(y_train, y_pred_train, multioutput='raw_values')

In [ ]:
print('\n All results:')
print(grid_obj_xgb.cv_results_)
print('\n Best estimator:')
print(grid_obj_xgb.best_estimator_)
print('\n Best hyperparameters:')
print(grid_obj_xgb.best_params_)
results = pd.DataFrame(grid_obj_xgb.cv_results_)#

In [ ]:
seed = 7
test_size = 0.2

X_train, X_test, y_train, y_test = train_test_split(X, Y, test_size=0.2, random_state=seed)
model = xgb.LGBMRegressor(base_score=0.5, booster='gbtree', colsample_bylevel=1,
             colsample_bynode=1, colsample_bytree=0.9, gamma=3, gpu_id=-1,
             importance_type='gain', interaction_constraints='',
             learning_rate=0.003, max_delta_step=0, max_depth=60,
             min_child_weight=40, monotone_constraints='()',
             n_estimators=10000, n_jobs=0, num_parallel_tree=1, random_state=30,
             reg_alpha=1, reg_lambda=5, scale_pos_weight=1, subsample=1,
             tree_method='exact', validate_parameters=1, verbosity=None)

eval_set = [(X_train, y_train), (X_test, y_test)]
model.fit(X_train, y_train, eval_metric=["mae", "rmse"], eval_set=eval_set, verbose=True, early_stopping_rounds=10)
y_pred = model.predict(X_test)
predictions = [value for value in y_pred]
predictions
results = model.evals_result()
epoch = len(results['validation_0']['mae'])
x_axis = range(0, epoch)
# plot log loss
fig, ax = pyplot.subplots()
ax.plot(x_axis, results['validation_0']['mae'], label='Train')
ax.plot(x_axis, results['validation_1']['mae'], label='Test')
ax.legend()
pyplot.ylabel('Mean Absolute Error')
pyplot.title('XGBoost MAE')
pyplot.savefig('XGBoost_MAE_tuned.png')
pyplot.show()
# plot classification error
fig, ax = pyplot.subplots()
ax.plot(x_axis, results['validation_0']['rmse'], label='Train')
ax.plot(x_axis, results['validation_1']['rmse'], label='Test')
ax.legend()
pyplot.ylabel('Root Mean Square Error')
pyplot.title('XGBoost RMSE')
pyplot.savefig('XGBoost_RMSE_tuned.png')
pyplot.show()

In [ ]:
from sklearn.model_selection import cross_val_score, KFold
from sklearn.metrics import mean_absolute_error

scores = []
cv = KFold(n_splits=10, shuffle=True)
fig = plt.figure()
i = 1
for train, test in cv.split(X_train, y_train):
    prediction = model.fit(X_train.iloc[train],
                 y_train.iloc[train]).predict(X_train.iloc[test])
    true = y_train.iloc[test]
    score = mean_absolute_error(true, prediction)
    scores.append(score)
    plt.scatter(prediction, true, lw=2, alpha=0.3,
                label='Fold %d (MAE = %0.2f)' % (i,score))
    i = i+1
plt.plot([min(y_train),max(y_train)], [min(y_train),max(y_train)],
         linestyle='--', lw=2, color='black')
plt.xlabel('Predicted Value')
plt.ylabel('Actual Value')
plt.title('K-Fold Validation')
plt.legend(prop={"size":10}, loc='center left', bbox_to_anchor=(1, 0.5))
plt.savefig('K-fold_Validation_MAE.png')
plt.show()

In [ ]:
from sklearn import metrics
## Kpi
print("R2 (explained variance):", round(metrics.r2_score(y_test, predictions), 2))
print("Mean Absolute Perc Error (Σ(|y-pred|/y)/n):", round(np.mean(np.abs((y_test-predictions)/predictions)), 2))
print("Mean Absolute Error (Σ|y-pred|/n):", "{:,.2f}".format(metrics.mean_absolute_error(y_test, predictions)))
print("Root Mean Squared Error (sqrt(Σ(y-pred)^2/n)):", "{:,.2f}".format(np.sqrt(metrics.mean_squared_error(y_test, predictions))))
## residuals
residuals = []
for i, c in zip(y_test, y_pred):
    residuals.append(i - c)

In [ ]:
max_error = max(residuals) if abs(max(residuals)) > abs(min(residuals)) else min(residuals)
max_idx = list(residuals).index(max(residuals)) if abs(max(residuals)) > abs(min(residuals)) else list(residuals).index(min(residuals))
max_true, max_pred = y_test.iloc[max_idx], y_pred[max_idx]
print("Max Error:", "{:,.0f}".format(max_error))

In [ ]:
print(y_test.iloc[20] - y_pred[20])

In [ ]:
fig, ax = plt.subplots(nrows=1, ncols=2)
from statsmodels.graphics.api import abline_plot
ax[0].scatter(y_pred, y_test, color="black")
abline_plot(intercept=0, slope=1, color="red", ax=ax[0])
ax[0].vlines(x=max_pred, ymin=max_true, ymax=max_true-max_error, color='red', linestyle='--', alpha=0.7, label="max error")
ax[0].grid(True)
ax[0].set(xlabel="Predicted", ylabel="True", title="Predicted vs True")
ax[0].legend()

## Plot predicted vs residuals
ax[1].scatter(y_pred, residuals, color="red")
ax[1].vlines(x=max_pred, ymin=0, ymax=max_error, color='black', linestyle='--', alpha=0.7, label="max error")
ax[1].grid(True)
ax[1].set(xlabel="Predicted", ylabel="Residuals", title="Predicted vs Residuals")
ax[1].hlines(y=0, xmin=np.min(y_pred), xmax=np.max(y_pred))
ax[1].legend()
plt.savefig("residuals_fit.jpg")
plt.show()

In [ ]:
import seaborn as sns
fig, ax = plt.subplots()
sns.distplot(residuals, color="red", hist=True, kde=True, kde_kws={"shade":True}, ax=ax)
ax.grid(True)
ax.set(yticks=[], yticklabels=[], title="Residuals distribution")
plt.savefig('Residuals_distribution.png')
plt.show()


In [ ]:
## Importance
X_train, X_test, Y_train, Y_test = train_test_split(X, Y, test_size = 0.2)
# Build the model with the random forest regression algorithm:
model.fit(X_train, Y_train)

In [ ]:
import shap

In [ ]:
shap_values = shap.Explainer(model).shap_values(X_train)
shap.summary_plot(shap_values, X_train, plot_type="bar")
plt.savefig("summary_plot2.png")

In [ ]:
import matplotlib.pyplot as plt
f = plt.figure()
shap.summary_plot(shap_values, X_train)
f.savefig("summary_plot1.png", bbox_inches='tight', dpi=600)

In [ ]:
import lazypredict
print(lazypredict.__version__)


In [ ]:
import eli5
from eli5.sklearn import PermutationImportance

perm = PermutationImportance(model, random_state=1).fit(X_test, y_test)
eli5.show_weights(perm, feature_names = X_test.columns.tolist())

In [ ]:
n_fold = [2, 3, 4, 5, 6, 7, 8, 9, 10]
for fold in n_fold:
    scores = []
    cv = KFold(n_splits=fold, shuffle=True)
    fig = plt.figure()
    i = 1
    for train, test in cv.split(X, Y):
        prediction = model.fit(X.iloc[train],
                     Y.iloc[train]).predict(X.iloc[test])
        true = Y.iloc[test]
        score = mean_absolute_error(true, prediction)
        scores.append(score)
        plt.scatter(prediction, true, lw=2, alpha=0.3,
                    label='Fold %d (MAE = %0.2f)' % (i,score))
        i = i+1
    plt.plot([min(Y),max(Y)], [min(Y),max(Y)],
             linestyle='--', lw=2, color='black')
    plt.xlabel('Predicted Value')
    plt.ylabel('Actual Value')
    plt.title('K-Fold Validation')
    plt.legend(prop={"size":10}, loc='center left', bbox_to_anchor=(1, 0.5))
    plt.show()
    print("Average of CV:", mean(scores))
    print("All Scores of CV", scores)

